<h1>Содержание<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Обзор-и-подготовка-данных" data-toc-modified-id="Обзор-и-подготовка-данных-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Обзор и подготовка данных</a></span></li><li><span><a href="#Предсказание-запаса-сырья" data-toc-modified-id="Предсказание-запаса-сырья-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>Предсказание запаса сырья</a></span></li><li><span><a href="#Подготовка-к-расчёту-прибыли" data-toc-modified-id="Подготовка-к-расчёту-прибыли-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Подготовка к расчёту прибыли</a></span></li><li><span><a href="#Расчёт-суммарной-прибыли" data-toc-modified-id="Расчёт-суммарной-прибыли-4"><span class="toc-item-num">4&nbsp;&nbsp;</span>Расчёт суммарной прибыли</a></span></li><li><span><a href="#Определение-региона-для-разработки" data-toc-modified-id="Определение-региона-для-разработки-5"><span class="toc-item-num">5&nbsp;&nbsp;</span>Определение региона для разработки</a></span></li></ul></div>

# Выбор локации для скважин

**Цель работы** — рекомендовать нефтедобывающей компании регион для разработки новых скважин, основываясь на предсказаниях ML-модели о прогнозируемых прибыли и убытках.

**Ход работы**

Загрузим файлы и подготовим данные к дальнейшей работе модели.

Обучим и проверим модели отдельно для каждого из представленных регионов, после чего подготовимся к расчёту прибыли, подсчитав для начала минимально необходимый объём сырья для безубыточной разработки скважины.

Далее напишем функцию для получения суммарной прибыли для региона c наиболее продуктивных по расчетам скважин.

Итогом работы будет предложение конкретного региона для разработки на основе информации об ожидаемых средней прибыли и убытках.
 
Подводя итог, можно выделить пять этапов работы:
 1. Обзор и подготовка данных.
 2. Предсказание запаса сырья.
 3. Подготовка к расчёту прибыли.
 4. Расчёт суммарной прибыли.
 5. Определение региона для разработки. 

## Обзор и подготовка данных

Изучим данные и подготовим их к дальнейшему использованию моделью.

In [1]:
# импорт библиотек и фиксирование параметров
import numpy as np
import pandas as pd
import ydata_profiling as pp
import plotly.express as px

from itertools import product
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error

import plotly.io as pio
pio.renderers.default = "notebook_connected"

c:\ProgramData\Anaconda3\envs\practicum\lib\site-packages\numba\core\decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)
c:\ProgramData\Anaconda3\envs\practicum\lib\site-packages\visions\backends\shared\nan_handling.py:51: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  def hasna(x: np.ndarray) -> bool:


In [2]:
# чтение csv-файлов и создание датафреймов
first_reg = pd.read_csv('data_geo_1_reg.csv')
second_reg = pd.read_csv('data_geo_2_reg.csv')
third_reg = pd.read_csv('data_geo_3_reg.csv')

# получение случайных 10 строк и общей информации о датасетах
tables = [first_reg, second_reg, third_reg]
for table in tables:
    display(table.sample(10, random_state=3))
    print(table.info())

id        f0        f1        f2     product
79528  YR5Sg -0.798439  0.722815  4.118091   41.814811
53876  BM7Bi -0.002794  0.205051  9.470505  176.405978
9777   8LTWe  1.512459 -0.476273  5.184697  120.623946
6167   JqjWa -0.640949  0.995210  1.945188   82.960587
22020  nkbfL  0.557036  0.627157  1.865511   80.699074
85042  3qbwS  0.107193  1.089834  2.280330   70.178564
14758  exwHp -0.088408  0.946121 -1.792330   65.180298
65017  F6trP  0.120126 -0.057445  3.241555  144.041599
97903  xtMeE  0.075616  0.134591  1.215901  147.200787
84654  bpI7f  0.464947 -0.421461  5.112939  101.084516

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB
None


id         f0        f1        f2     product
79528  ClrkH  -9.616990 -9.950219  4.002589  110.992147
53876  9wmox -18.551131 -4.225997  3.994248  110.992147
9777   GsSUg  -7.892128 -1.735237  2.000742   57.085625
6167   SzJZ7   7.678503 -7.447216 -0.005827    0.000000
22020  TGYVO   5.578830 -8.187399  4.991929  137.945408
85042  kGFFF   2.506265 -4.237979 -0.010883    0.000000
14758  4YlRS   4.340559 -3.850164  4.999748  134.766305
65017  kO05w  -5.723916 -2.731296  2.006033   53.906522
97903  qGItQ  16.261450 -9.729375  0.995371   26.953261
84654  32734  -6.226435 -8.479210  0.997974   30.132364

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB
None


id        f0        f1         f2     product
79528  IzPst  0.194647  2.469580   0.458417   56.324969
53876  Og4zw -3.099415  3.781137   3.376006  159.510230
9777   J2FB8 -0.432362  0.228315   5.840886  106.784053
6167   hKW1X -1.095537 -0.854953   8.423223  122.134032
22020  K7U15  1.794371 -0.820678  10.475420  120.791430
85042  ggXMK  0.294920 -0.482935   1.391220   38.981639
14758  pnsAQ  0.830345  1.204876   1.403620   83.242309
65017  8O0fw  3.266574  0.714168   3.840849  120.457457
97903  GDVoJ -0.586365  1.103559   2.389679  106.010855
84654  OOux6 -2.497178  1.119071  -3.205636   94.972974

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100000 entries, 0 to 99999
Data columns (total 5 columns):
 #   Column   Non-Null Count   Dtype  
---  ------   --------------   -----  
 0   id       100000 non-null  object 
 1   f0       100000 non-null  float64
 2   f1       100000 non-null  float64
 3   f2       100000 non-null  float64
 4   product  100000 non-null  float64
dtypes: float64(4), object(1)
memory usage: 3.8+ MB
None


In [3]:
# проведение EDA
pp.ProfileReport(first_reg)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
# проведение EDA
pp.ProfileReport(second_reg)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
# проведение EDA
pp.ProfileReport(third_reg)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

По результатам проведённого обзора данных можно сделать вывод, что в рамках подготовки стоит совершить следующие операции с датасетами:
* Избавиться от задвоенной информации об одних и тех же скважинах
* Масштабировать признаки с помощью стандартизации

Значения, обнаруженные для некоторых дублирующих записей об одних и тех же скважинах, заменим на средние.

In [6]:
# замена значений
for table in tables:
    for column, ids in product(
        table.columns[1:],
        table.loc[table['id'].duplicated(), 'id']
    ):
        table.loc[
            table['id']==ids,
            column
        ] = table.loc[
            table['id']==ids,
            column
        ].mean()
    table.drop_duplicates(inplace=True)

# проверка изменений
for table in tables:
    print(table.id.duplicated().sum())

0
0
0


In [7]:
# разделение данных на выборки
fr_features = first_reg.drop(['product', 'id'], axis=1)
fr_target = first_reg['product']
fr_features_train, fr_features_valid, fr_target_train, fr_target_valid = (
    train_test_split(
        fr_features,
        fr_target,
        test_size=.25,
        random_state=3
    )
)
sr_features = second_reg.drop(['product', 'id'], axis=1)
sr_target = second_reg['product']
sr_features_train, sr_features_valid, sr_target_train, sr_target_valid = (
    train_test_split(
        sr_features,
        sr_target,
        test_size=.25,
        random_state=3
    )
)
tr_features = third_reg.drop(['product', 'id'], axis=1)
tr_target = third_reg['product']
tr_features_train, tr_features_valid, tr_target_train, tr_target_valid = (
    train_test_split(
        tr_features,
        tr_target,
        test_size=.25,
        random_state=3
    )
)
# проверка размеров выборок
print(
    'Размеры обучающей выборки первого региона:',
    fr_features_train.shape,
    fr_target_train.shape
    )
print(
    'Размеры валидационной выборки первого региона:',
    fr_features_valid.shape,
    fr_target_valid.shape
    )
print()
print(
    'Размеры обучающей выборки второго региона:',
    sr_features_train.shape,
    sr_target_train.shape
    )
print(
    'Размеры валидационной выборки второго региона:',
    sr_features_valid.shape,
    sr_target_valid.shape
    )
print()
print(
    'Размеры обучающей выборки третьего региона:',
    tr_features_train.shape,
    tr_target_train.shape
    )
print(
    'Размеры валидационной выборки третьего региона:',
    tr_features_valid.shape,
    tr_target_valid.shape
    )

Размеры обучающей выборки первого региона: (74992, 3) (74992,)
Размеры валидационной выборки первого региона: (24998, 3) (24998,)

Размеры обучающей выборки второго региона: (74997, 3) (74997,)
Размеры валидационной выборки второго региона: (24999, 3) (24999,)

Размеры обучающей выборки третьего региона: (74997, 3) (74997,)
Размеры валидационной выборки третьего региона: (24999, 3) (24999,)


In [8]:
# маштабирование признаков
features_train = [
    fr_features_train,
    sr_features_train,
    tr_features_train
]
features_valid = [
    fr_features_valid,
    sr_features_valid,
    tr_features_valid
]
for train, valid in zip(features_train, features_valid):
    scaler = StandardScaler()
    scaler.fit(train)
    train = scaler.transform(train)
    valid = scaler.transform(valid)

**Промежуточные итоги**

По итогам обзора данных они были предобработаны (удалена дублирующая информация) и подготовлены для дальнейшего обучения с помощью масштабирования признаков.

## Предсказание запаса сырья

С помощью линейных моделей, оценивая их качество, предскажем для каждого региона ожидаемый запас сырья для новых скважин, сравним средние показатели.

In [9]:
# обучение модели и получение предсказаний для первого региона
fr_reg = LinearRegression(n_jobs=-1)
fr_reg.fit(fr_features_train, fr_target_train)
fr_predictions = fr_reg.predict(fr_features_valid)

# обучение модели и получение предсказаний для второго региона
sr_reg = LinearRegression(n_jobs=-1)
sr_reg.fit(sr_features_train, sr_target_train)
sr_predictions = sr_reg.predict(sr_features_valid)

# обучение модели и получение предсказаний для третьего региона
tr_reg = LinearRegression(n_jobs=-1)
tr_reg.fit(tr_features_train, tr_target_train)
tr_predictions = tr_reg.predict(tr_features_valid)

In [10]:
# получение средних объёмов сырья и RMSE моделей
fr_mean_pr = fr_predictions.mean()
sr_mean_pr = sr_predictions.mean()
tr_mean_pr = tr_predictions.mean()

print(
    'Средний запас сырья в новой скважине в первом регионе:',
    f'{fr_mean_pr:.3f} тыс. баррелей'
)
print(
    'RMSE модели для первого региона',
    f'{mean_squared_error(fr_target_valid, fr_predictions, squared=False):.3f}'
)
print()
print(
    'Средний запас сырья в новой скважине во втором регионе:',
    f'{sr_mean_pr:.3f} тыс. баррелей'
)
print(
    'RMSE модели для второго региона',
    f'{mean_squared_error(sr_target_valid, sr_predictions, squared=False):.3f}'
)
print()
print(
    'Средний запас сырья в новой скважине в третьем регионе:',
    f'{tr_mean_pr:.3f} тыс. баррелей'
)
print(
    'RMSE модели для третьего региона',
    f'{mean_squared_error(tr_target_valid, tr_predictions, squared=False):.3f}'
)

Средний запас сырья в новой скважине в первом регионе: 92.436 тыс. баррелей
RMSE модели для первого региона 37.697

Средний запас сырья в новой скважине во втором регионе: 68.857 тыс. баррелей
RMSE модели для второго региона 0.890

Средний запас сырья в новой скважине в третьем регионе: 95.073 тыс. баррелей
RMSE модели для третьего региона 39.756


**Промежуточные выводы**

Учитывая, что во втором регионе `f2`-показатель, так же, как и целевой признак, распределены не равномерно, а сильно дискретно, RMSE модели для второго региона минимальна — 890 баррелей.
Причинами могли послужить, например, отличающиеся от остальных двух регионов формат сбора данных, способ обработки, просчёта, хранения итоговых показателей или же методы, применяемые технологии разработки в принципе.

И хотя средний прогнозируемый запас для скважины в первом и третьем регионах на 23-27 тыс. баррелей выше аналогичного во втором регионе, ошибка второго меньше на 37-38 тыс. баррелей.

## Подготовка к расчёту прибыли

Расчитаем минимальный объём сырья для безубыточной разработки новой скважины. Сравним с полученными ранее средними результататми по регионам.

В начале разработки региона выбирают 200 скважин. Общий бюджет на их разработку для каждого региона — 10 млрд рублей. Доход с каждой единицы продукта составляет 450 тыс. рублей.

In [11]:
# получение объёма сырья для безубыточной разработки
WELLS_AMOUNT = 200
BUDGET = 10_000_000_000
UNIT_INCOME = 450_000
breakeven_oil_volume = BUDGET / WELLS_AMOUNT / UNIT_INCOME

print(
    'Безубыточный объём сырья для скважины:',
    f'{breakeven_oil_volume:.3f} тыс. баррелей'
)
print()
if fr_mean_pr < breakeven_oil_volume:
    print('Средний запас предсказанного сырья в первом регионе убыточен')
else:
    print('Средний запас предсказанного сырья в первом регионе безубыточен')
print()
if sr_mean_pr < breakeven_oil_volume:
    print('Средний запас предсказанного сырья во втором регионе убыточен')
else:
    print('Средний запас предсказанного сырья во втором регионе безубыточен')
print()
if tr_mean_pr < breakeven_oil_volume:
    print('Средний запас предсказанного сырья в третьем регионе убыточен')
else:
    print('Средний запас предсказанного сырья в третьем регионе безубыточен')

Безубыточный объём сырья для скважины: 111.111 тыс. баррелей

Средний запас предсказанного сырья в первом регионе убыточен

Средний запас предсказанного сырья во втором регионе убыточен

Средний запас предсказанного сырья в третьем регионе убыточен


**Промежуточные выводы**

Для безубыточной разработки средний запас сырья в скважине должен составлять 111 с небольшим тыс. бареллей, что ощутимо выше, чем средний прогнозируемый объём нефти в скважине для любого региона, полученный на предыдущем этапе. Для дальнейшей оценки предсказаний модели воспользуемся другим подходом.

## Расчёт суммарной прибыли

Сначала напишем функцию для расчёта общей прибыли в регионе с выбранного количества скважин, используя реальные исторические показатели скважин, наиболее продуктивных по предсказаниям модели.

In [12]:
# определение функции для подсчёта прибыли
def profit(target, predictions, count):
    sorted_preds = predictions.sort_values(ascending=False)
    selected = target[sorted_preds.index][:count]
    return UNIT_INCOME * selected.sum() - BUDGET

## Определение региона для разработки

Для итогового выбора региона для разработки воспользуемся техникой bootstrap, формирующей множество различных выборок из генеральной совокупности всех сважин региона. На основании данных о выручке по этим выборкам получим среднюю прибыль, 95%-й доверительный интервал и риск убытков в каждом регионе. У выбранного региона должна быть наибольшая средняя прибыль при вероятности убытков меньше 2.5%

In [13]:
# получение средних значений прибыли, доверительного интервала и рисков убытков
state = np.random.RandomState(3)
targets = [
    fr_target_valid.reset_index(drop=True),
    sr_target_valid.reset_index(drop=True),
    tr_target_valid.reset_index(drop=True)
]
preds = [
    pd.Series(fr_predictions),
    pd.Series(sr_predictions),
    pd.Series(tr_predictions)
]

number = 0
df = pd.DataFrame()
for trt, prediction in zip(targets, preds):
    values = []
    number += 1
    for i in range(1000):
        target_subsample = trt.sample(
            500,
            replace=True,
            random_state=state
        )
        preds_subsample = prediction[target_subsample.index]
        values.append(
            profit(
                target_subsample,
                preds_subsample,
                WELLS_AMOUNT
            )
        )
    values = pd.Series(values)
    lower = values.quantile(0.025)
    upper = values.quantile(0.975)
    row = {
        'region':number,
        'revenue':values.mean(),
        'is_unprofitable':(lower < 0).astype('str')
    }
    df = df.append(row, ignore_index=True)
    print(
        f'Средняя прибыль региона {number}:',
        '{:,.2f}'.format(values.mean()).replace(',', ' '),
        'руб.'
    )
    print(
        f'95%-й доверительный интервал в регионе {number}:',
        '{:,.2f}'.format(lower).replace(',', ' '),
        '— {:,.2f}'.format(upper).replace(',', ' '),
        'руб.'
    )
    if lower < 0:
        print(
            f'Вероятность убытков в регионе {number} не меньше эталонных 2.5%',
            f'— {(len(values[values.values<0]) / len(values)):.1%}'
        )
    else:
        print(
            f'Вероятность убытков в регионе {number} меньше эталонных 2.5%',
            f'— {(len(values[values.values<0]) / len(values)):.1%}'
        )
    print()
df['region'] = df['region'].astype('int').astype('str')

Средняя прибыль региона 1: 483 229 752.71 руб.
95%-й доверительный интервал в регионе 1: -75 279 474.02 — 1 020 231 568.89 руб.
Вероятность убытков в регионе 1 не меньше эталонных 2.5% — 5.3%

Средняя прибыль региона 2: 531 711 700.41 руб.
95%-й доверительный интервал в регионе 2: 120 231 627.60 — 949 285 428.68 руб.
Вероятность убытков в регионе 2 меньше эталонных 2.5% — 0.4%

Средняя прибыль региона 3: 432 297 047.61 руб.
95%-й доверительный интервал в регионе 3: -116 124 677.04 — 1 006 918 389.22 руб.
Вероятность убытков в регионе 3 не меньше эталонных 2.5% — 6.1%



In [14]:
# получение графика прибыли регионов
px.bar(
    df,
    x='region',
    y='revenue',
    color='is_unprofitable',
    color_discrete_sequence=px.colors.qualitative.Light24,
    text_auto=True,
    width=900,
    height=500,
    title='Средняя прибыль по регионам'
).update_layout(
    xaxis_title='Регион',
    yaxis_title='Прибыль, млн руб.',
    legend_title='Высокая вероятность убытков'
)

**Итоговый вывод**

Требуемому условию низких рисков убытков при разработке соответствует только один регион — второй. Он же показывает и максимальную ожидаемую прибыль. Следовательно, именно его можно в итоге рекомендовать для разработки новых скважин.
Также, если отличие в распределении показателей у второго региона завистит не от разницы в сборе и подсчёте показаний, а от контролиреумых компанией методов и технологий добычи сырья, то можно посоветовать изучить вопрос влияния последних более подробно, так как они могут влиять на продуктивность и прибыльность добычи. В таком случае стоит применять используемые во втором регионе методы и технологии при дальнейшей разработке и добыче в месторождениях компании.